# Accessing CLMS API
https://eea.github.io/clms-api-docs/download.html

## vSensor

In [1]:
import requests
import json
import xarray as xr
import rasterio as rio
import osgeo
import time
import jwt

API="https://land.copernicus.eu/api/"
VERSION="v1"
PRODUCT="CORINE-Land-Cover"

# Load saved key from filesystem
service_key = json.load(open('../references/corine/clc.json', 'rb'))

private_key = service_key['private_key'].encode('utf-8')

claim_set = {
    "iss": service_key['client_id'],
    "sub": service_key['user_id'],
    "aud": service_key['token_uri'],
    "iat": int(time.time()),
    "exp": int(time.time() + (60 * 60)),
}
grant = jwt.encode(claim_set, private_key, algorithm='RS256')

result = requests.post(
        service_key["token_uri"],
        headers={
            "Accept": "application/json",
            "Content-Type": "application/x-www-form-urlencoded",
        },
        data={
            "grant_type": "urn:ietf:params:oauth:grant-type:jwt-bearer",
            "assertion": grant,
        },
)

access_token_info_json = result.json()
access_token = access_token_info_json.get('access_token')
print(access_token)


W9LS0hsZ6Gs8F8mztO6Earivt9UcX3oSRzptl8ZDmxHwLJvyU18mItaQ-ZXkzHmiuAl9jvzzHXQFzBW7BiGUgg==


In [22]:
req1= requests.post(f'{API}@@oauth2-token', headers={'Accept': 'application/json', 'Content-Type': 'application/x-www-form-urlencoded'}, data='grant_type=urn%3Aietf%3Aparams%3Aoauth%3Agrant-type%3Ajwt-bearer&assertion=REDACTED')
req1.json()
req2= requests.get(f'{API}@search?portal_type=DataSet', headers={'Accept': 'application/json', 'Authorization': 'Bearer <REDACTED>'})
req2.json()

TypeError: Session.request() got an unexpected keyword argument 'b_size'

In [2]:
req3=requests.get(f'{API}@search?portal_type=DataSet&metadata_fields=UID&metadata_fields=dataset_full_format&&metadata_fields=dataset_download_information&&b_size=100000', headers={'Accept': 'application/json'})
req3.json()

{'@id': 'https://land.copernicus.eu/api/@search?portal_type=DataSet&metadata_fields=UID&metadata_fields=dataset_full_format&metadata_fields=dataset_download_information',
 'items': [{'@id': 'https://land.copernicus.eu/api/en/products/european-ground-motion-service/egms-basic',
   '@type': 'DataSet',
   'UID': '00f7264e92d54a70b02bce9b315d7b32',
   'dataset_download_information': {'items': []},
   'dataset_full_format': None,
   'description': 'Provides InSAR displacement data provided in the satellite Line-of-Sight, with annotated geo-localisation and quality measures per measurement point. The dataset is generated from the interferometric analysis of Sentinel-1 radar images at full resolution (20x5 m).   EGMS Basic is visualised as a vector map of measurement points colour-coded by average line-of-sight velocity and distributed to users in comma-separated values format. Each point is associated with a time series of displacement, i.e. a plot with values of displacement per acquisition

In [6]:
with open('../references/corine/clms-docs.json', 'w') as f:
    json.dump(req3.json(), f)

In [3]:
clc = req3.json()['items']
substrings = ['CORINE Land Cover', 'Europe', '100 m', '6-yearly']
for data in clc:
    if (substrings[0] in data['title']) & (substrings[2] in data['title']) & (substrings[3] in data['title']) & ('Change' not in data['title']):
        print(data['title'])
        print(data['dataset_full_format'])
        print(data['dataset_download_information'])
        print(data['UID'])
        print(data['@id'])

CORINE Land Cover 2018 (vector/raster 100 m), Europe, 6-yearly
None
{'items': [{'@id': '1bda2fbd-3230-42ba-98cf-69c96ac063bc', 'full_format': 'GDB', 'full_path': 'H:\\Corine_Land_Cover\\Corine_Land_Cover\\Corine_Land_Cover(CLC)_2018\\CLC2018_Version_20\\Data\\data-master\\U2018_CLC2018_V2020_20u1_vector\\U2018_CLC2018_V2020_20u1.gdb', 'full_source': 'EEA', 'name': 'VECTOR'}, {'@id': '7bcdf9d1-6ba0-4d4e-afa8-01451c7316cb', 'collection': '100 m', 'full_format': 'Geotiff', 'full_path': 'H:\\Corine_Land_Cover\\Corine_Land_Cover\\Corine_Land_Cover(CLC)_2018\\CLC2018_Version_20\\Data\\data-master\\U2018_CLC2018_V2020_20u1_raster100m_tiled', 'full_source': 'EEA', 'name': 'RASTER'}]}
0407d497d3c44bcd93ce8fd5bf78596a
https://land.copernicus.eu/api/en/products/corine-land-cover/clc2018
CORINE Land Cover 2012 (vector/raster 100 m), Europe, 6-yearly
GDB
{'items': [{'@id': 'cff14ee5-bafb-46f4-a1b2-2cd6f4049514', 'full_format': {'title': 'GDB', 'token': 'GDB'}, 'full_path': 'H:\\Corine_Land_Cover\\C

In [4]:
import glob
import os

current =[]
new = []
obj = {}
for data in clc:
        if (substrings[0] in data['title']) & (substrings[2] in data['title']) & (substrings[3] in data['title']) & ('Change' not in data['title']):
            obj['title']=data['title']
            obj['dataset_full_format']=data['dataset_full_format']
            obj['dataset_download_information']=data['dataset_download_information']
            obj['UID']=data['UID']
            obj['@id']=data['@id']
            current.append(obj)
            obj = {}

list_of_files = glob.glob('../logs/feedback/corine/*.json') # * means all if need specific format then *.csv
latest_file = max(list_of_files, key=os.path.getctime)
    
if latest_file:
        with open(latest_file, 'r') as f:
            old = json.load(f)
            for i in new:
                if i not in old:
                    new.append(i) 
                    print('new CORINE data available...')
                else:
                    print('no new data')
            with open(f'../logs/feedback/corine/clms-{round(time.time())}.json', 'w') as f:
                json.dump(new, f)
    


## Intaker

In [5]:
current

[{'title': 'CORINE Land Cover 2018 (vector/raster 100 m), Europe, 6-yearly',
  'dataset_full_format': None,
  'dataset_download_information': {'items': [{'@id': '1bda2fbd-3230-42ba-98cf-69c96ac063bc',
     'full_format': 'GDB',
     'full_path': 'H:\\Corine_Land_Cover\\Corine_Land_Cover\\Corine_Land_Cover(CLC)_2018\\CLC2018_Version_20\\Data\\data-master\\U2018_CLC2018_V2020_20u1_vector\\U2018_CLC2018_V2020_20u1.gdb',
     'full_source': 'EEA',
     'name': 'VECTOR'},
    {'@id': '7bcdf9d1-6ba0-4d4e-afa8-01451c7316cb',
     'collection': '100 m',
     'full_format': 'Geotiff',
     'full_path': 'H:\\Corine_Land_Cover\\Corine_Land_Cover\\Corine_Land_Cover(CLC)_2018\\CLC2018_Version_20\\Data\\data-master\\U2018_CLC2018_V2020_20u1_raster100m_tiled',
     'full_source': 'EEA',
     'name': 'RASTER'}]},
  'UID': '0407d497d3c44bcd93ce8fd5bf78596a',
  '@id': 'https://land.copernicus.eu/api/en/products/corine-land-cover/clc2018'},
 {'title': 'CORINE Land Cover 2012 (vector/raster 100 m), Europe

In [22]:
# no longer working as of 2024-06-05
download_list = []
for i in current:
    DatasetID = i['UID']
    DatasetDownloadInformationID = ''

    for x in i['dataset_download_information']['items']:
        if x['full_format'] == 'Geotiff':
            DatasetDownloadInformationID = x['@id']
    print(DatasetID)
    print(DatasetDownloadInformationID)           
    download_obj= {'DatasetID': DatasetID, 'DatasetDownloadInformationID': DatasetDownloadInformationID, 'OutputFormat': 'Geotiff', 'OutputGCS': 'EPSG:4326'}
    download_list.append(download_obj)
    
task=requests.post(f'{API}@datarequest_post', headers={'Accept': 'application/json', 'Content-Type': 'application/json', 'Authorization': f'Bearer {access_token}'}, json={'Datasets':download_list})
print(task.json())

0407d497d3c44bcd93ce8fd5bf78596a
7bcdf9d1-6ba0-4d4e-afa8-01451c7316cb
a5ee71470be04d66bcff498f94ceb5dc
b1027c88-6256-435b-98a3-62f019cbb381
d443c86fec2f49e08ff12c7decdbf2af
4841f8cb-6e7c-4227-bb35-cd787609c546
6704f90ca82e4f228a46111519f8978e
19d7fbd8-53ee-4d09-89b6-fe5231247763
8b393c8e474642d5acb4ed70fc2dc024
fecff4c7-a5e5-428d-817d-a8ee5f23d99d
{'msg': 'To download the full dataset, please download it through the corresponding pre-packaged data collection', 'status': 'error'}


In [23]:
download_list

[{'DatasetID': '0407d497d3c44bcd93ce8fd5bf78596a',
  'DatasetDownloadInformationID': '7bcdf9d1-6ba0-4d4e-afa8-01451c7316cb',
  'OutputFormat': 'Geotiff',
  'OutputGCS': 'EPSG:4326'},
 {'DatasetID': 'a5ee71470be04d66bcff498f94ceb5dc',
  'DatasetDownloadInformationID': 'b1027c88-6256-435b-98a3-62f019cbb381',
  'OutputFormat': 'Geotiff',
  'OutputGCS': 'EPSG:4326'},
 {'DatasetID': 'd443c86fec2f49e08ff12c7decdbf2af',
  'DatasetDownloadInformationID': '4841f8cb-6e7c-4227-bb35-cd787609c546',
  'OutputFormat': 'Geotiff',
  'OutputGCS': 'EPSG:4326'},
 {'DatasetID': '6704f90ca82e4f228a46111519f8978e',
  'DatasetDownloadInformationID': '19d7fbd8-53ee-4d09-89b6-fe5231247763',
  'OutputFormat': 'Geotiff',
  'OutputGCS': 'EPSG:4326'},
 {'DatasetID': '8b393c8e474642d5acb4ed70fc2dc024',
  'DatasetDownloadInformationID': 'fecff4c7-a5e5-428d-817d-a8ee5f23d99d',
  'OutputFormat': 'Geotiff',
  'OutputGCS': 'EPSG:4326'}]

In [13]:
for i in current:
    DatasetID = i['UID']
    DatasetDownloadInformationID = ''

    for x in i['dataset_download_information']['items']:
        if x['full_format'] == 'Geotiff':
            DatasetDownloadInformationID = x['@id']
    print(DatasetID)
    print(DatasetDownloadInformationID)           
    task=requests.post(f'{API}@get-download-file-urls?dataset_uid={DatasetID}&file_id{DatasetDownloadInformationID}', headers={'Accept': 'application/json', 'Authorization': f'Bearer {access_token}'})
    print(task.json())

0407d497d3c44bcd93ce8fd5bf78596a
7bcdf9d1-6ba0-4d4e-afa8-01451c7316cb
{'message': 'Resource not found: https://land.copernicus.eu/api/@get-download-file-urls', 'type': 'NotFound'}
a5ee71470be04d66bcff498f94ceb5dc
b1027c88-6256-435b-98a3-62f019cbb381
{'message': 'Resource not found: https://land.copernicus.eu/api/@get-download-file-urls', 'type': 'NotFound'}
d443c86fec2f49e08ff12c7decdbf2af
4841f8cb-6e7c-4227-bb35-cd787609c546
{'message': 'Resource not found: https://land.copernicus.eu/api/@get-download-file-urls', 'type': 'NotFound'}
6704f90ca82e4f228a46111519f8978e
19d7fbd8-53ee-4d09-89b6-fe5231247763
{'message': 'Resource not found: https://land.copernicus.eu/api/@get-download-file-urls', 'type': 'NotFound'}
8b393c8e474642d5acb4ed70fc2dc024
fecff4c7-a5e5-428d-817d-a8ee5f23d99d
{'message': 'Resource not found: https://land.copernicus.eu/api/@get-download-file-urls', 'type': 'NotFound'}


In [2]:
status=requests.get(f'{API}@datarequest_search', headers={'Accept': 'application/json', 'Content-Type': 'application/json', 'Authorization': f'Bearer {access_token}'})
print(status.json())
with open('../references/corine/status-sample-3.json', 'w') as f:
    json.dump(status.json(), f)

{'40569095338': {'Datasets': [{'DatasetFormat': 'Geotiff', 'DatasetID': '0407d497d3c44bcd93ce8fd5bf78596a', 'DatasetPath': 'SDpcQ29yaW5lX0xhbmRfQ292ZXJcQ29yaW5lX0xhbmRfQ292ZXJcQ29yaW5lX0xhbmRfQ292ZXIoQ0xDKV8yMDE4XENMQzIwMThfVmVyc2lvbl8yMFxEYXRhXGRhdGEtbWFzdGVyXFUyMDE4X0NMQzIwMThfVjIwMjBfMjB1MV9yYXN0ZXIxMDBtX3RpbGVk', 'DatasetSource': 'EEA', 'DatasetTitle': 'CORINE Land Cover 2018 (vector/raster 100 m), Europe, 6-yearly', 'Metadata': ['https://sdi.eea.europa.eu/catalogue/copernicus/api/records/960998c1-1870-4e82-8051-6485205ebbac/formatters/xml?approved=true', 'https://sdi.eea.europa.eu/catalogue/copernicus/api/records/71c95a07-e296-44fc-b22b-415f42acfdf0/formatters/xml?approved=true'], 'OutputFormat': 'Geotiff', 'OutputGCS': 'EPSG:4326', 'WekeoChoices': ''}], 'FMETaskId': 25480, 'RegistrationDateTime': '2023-11-13T14:14:01.323884', 'Status': 'In_progress', 'UserID': 'n00eckgi'}, '6040838668': {'Datasets': [{'DatasetFormat': 'Geotiff', 'DatasetID': '6704f90ca82e4f228a46111519f8978e', 'D

# Pre-packaged files

In [2]:
req4 = requests.get(f'{API}@search?portal_type=DataSet&metadata_fields=UID&metadata_fields=downloadable_files&metadata_fields=dataset_download_information&metadata_fields=download_limit_temporal_extent&metadata_fields=download_limit_area_extent&b_size=300', headers={'Accept': 'application/json'})
req4.json()

{'@id': 'https://land.copernicus.eu/api/@search?portal_type=DataSet&metadata_fields=UID&metadata_fields=downloadable_files&metadata_fields=dataset_download_information&metadata_fields=download_limit_temporal_extent&metadata_fields=download_limit_area_extent',
 'items': [{'@id': 'https://land.copernicus.eu/api/en/products/european-ground-motion-service/egms-basic',
   '@type': 'DataSet',
   'UID': '00f7264e92d54a70b02bce9b315d7b32',
   'dataset_download_information': {'items': []},
   'description': 'Provides InSAR displacement data provided in the satellite Line-of-Sight, with annotated geo-localisation and quality measures per measurement point. The dataset is generated from the interferometric analysis of Sentinel-1 radar images at full resolution (20x5 m).   EGMS Basic is visualised as a vector map of measurement points colour-coded by average line-of-sight velocity and distributed to users in comma-separated values format. Each point is associated with a time series of displacement

In [3]:
with open('../references/corine/clms-docs-prepackaged.json', 'w') as f:
    json.dump(req4.json(), f)

In [14]:
clc = req4.json()['items']
substrings = ['CORINE Land Cover', 'Europe', '100 m', '6-yearly']
for data in clc:
    if (substrings[0] in data['title']) & (substrings[2] in data['title']) & (substrings[3] in data['title']) & ('Change' not in data['title']):
        print(data['title'])
        #print(data['dataset_full_format'])
        #print(data['dataset_download_information'])
        print(data['UID'])
        print(data['downloadable_files'])

CORINE Land Cover 2018 (vector/raster 100 m), Europe, 6-yearly
0407d497d3c44bcd93ce8fd5bf78596a
{'items': [{'@id': '3d9e2413-46ca-4f6e-abf8-b6eb429a4e48', 'area': 'Europe', 'file': 'u2018_clc2018_v2020_20u1_raster100m', 'format': 'Geotiff', 'path': 'H:\\Corine_Land_Cover\\Corine_Land_Cover\\Corine_Land_Cover(CLC)_2018\\CLC2018_Version_20\\Data\\data-details\\raster\\u2018_clc2018_v2020_20u1_raster100m.zip', 'resolution': '100 m', 'size': '125 MB', 'source': 'EEA', 'title': '', 'type': 'Raster', 'version': 'v2020_20u1', 'year': ''}, {'@id': '3bfb1a41-8b59-425d-b172-bd44517adbca', 'area': 'Europe', 'file': 'u2018_clc2018_v2020_20u1_fgdb', 'format': 'GDB', 'path': 'H:\\Corine_Land_Cover\\Corine_Land_Cover\\Corine_Land_Cover(CLC)_2018\\CLC2018_Version_20\\Data\\data-details\\vector\\gdb\\u2018_clc2018_v2020_20u1_fgdb.zip', 'resolution': '', 'size': '5 GB', 'source': 'EEA', 'title': '', 'type': 'Vector', 'version': 'v2020_20u1', 'year': ''}, {'@id': '71a52224-0b24-4ecf-804c-a676c0017922', '

In [15]:
import glob
import os

current =[]
new = []
obj = {}
for data in clc:
        if (substrings[0] in data['title']) & (substrings[2] in data['title']) & (substrings[3] in data['title']) & ('Change' not in data['title']):
            obj['title']=data['title']
            #obj['dataset_full_format']=data['dataset_full_format']
            #obj['dataset_download_information']=data['dataset_download_information']
            obj['downloadable_files'] = data['downloadable_files']
            obj['UID']=data['UID']
            obj['@id']=data['@id']
            current.append(obj)
            obj = {}

list_of_files = glob.glob('../logs/feedback/corine/*.json') # * means all if need specific format then *.csv
latest_file = max(list_of_files, key=os.path.getctime)
    
if latest_file:
        with open(latest_file, 'r') as f:
            old = json.load(f)
            for i in new:
                if i not in old:
                    new.append(i) 
                    print('new CORINE data available...')
                else:
                    print('no new data')
            #with open(f'../logs/feedback/corine/clms-{round(time.time())}.json', 'w') as f:
                #json.dump(new, f)
    

In [17]:
# no longer working as of 2024-06-05
download_list = []
for i in current:
    DatasetID = i['UID']
    DatasetDownloadInformationID = ''

    for x in i['downloadable_files']['items']:
        if x['type'] == 'Raster':
            DatasetDownloadInformationID = x['@id']
    print(DatasetID)
    print(DatasetDownloadInformationID)           
    download_obj= {'DatasetID': DatasetID, 'FileID': DatasetDownloadInformationID, 'OutputFormat': 'Geotiff', 'OutputGCS': 'EPSG:4326'}
    download_list.append(download_obj)
    
task=requests.post(f'{API}@datarequest_post', headers={'Accept': 'application/json', 'Content-Type': 'application/json', 'Authorization': f'Bearer {access_token}'}, json={'Datasets':download_list})
print(task.json())

0407d497d3c44bcd93ce8fd5bf78596a
3d9e2413-46ca-4f6e-abf8-b6eb429a4e48
a5ee71470be04d66bcff498f94ceb5dc
9f992dad-d129-408e-be66-821adbd52a46
d443c86fec2f49e08ff12c7decdbf2af
56810bc2-a62d-46a4-a47e-e8e1de8df1b2
6704f90ca82e4f228a46111519f8978e
3ce937ab-9178-42b7-8000-60458100c38f
8b393c8e474642d5acb4ed70fc2dc024
95232d29-1273-4336-89b0-bddf75a059bf
{'ErrorTaskIds': [], 'TaskIds': [{'TaskID': '83949085000'}]}


In [18]:
status=requests.get(f'{API}@datarequest_search', headers={'Accept': 'application/json', 'Content-Type': 'application/json', 'Authorization': f'Bearer {access_token}'})
print(status.json())
with open('../references/corine/status-sample-3.json', 'w') as f:
    json.dump(status.json(), f)

{'40569095338': {'Datasets': [{'DatasetFormat': 'Geotiff', 'DatasetID': '0407d497d3c44bcd93ce8fd5bf78596a', 'DatasetPath': 'SDpcQ29yaW5lX0xhbmRfQ292ZXJcQ29yaW5lX0xhbmRfQ292ZXJcQ29yaW5lX0xhbmRfQ292ZXIoQ0xDKV8yMDE4XENMQzIwMThfVmVyc2lvbl8yMFxEYXRhXGRhdGEtbWFzdGVyXFUyMDE4X0NMQzIwMThfVjIwMjBfMjB1MV9yYXN0ZXIxMDBtX3RpbGVk', 'DatasetSource': 'EEA', 'DatasetTitle': 'CORINE Land Cover 2018 (vector/raster 100 m), Europe, 6-yearly', 'Metadata': ['https://sdi.eea.europa.eu/catalogue/copernicus/api/records/960998c1-1870-4e82-8051-6485205ebbac/formatters/xml?approved=true', 'https://sdi.eea.europa.eu/catalogue/copernicus/api/records/71c95a07-e296-44fc-b22b-415f42acfdf0/formatters/xml?approved=true'], 'OutputFormat': 'Geotiff', 'OutputGCS': 'EPSG:4326', 'WekeoChoices': ''}], 'FMETaskId': 25480, 'FinalizationDateTime': '2023-12-04T05:46:33.242442', 'Message': 'Try again later and if the error persists please contact the administrator (copernicus@eea.europa.eu)', 'RegistrationDateTime': '2023-11-13T14:1